In [20]:
import torch
from transformers import AutoTokenizer, AutoModelForSequenceClassification
import pandas as pd
import os
from time import gmtime, strftime
import torch.nn.functional as F
from tqdm import tqdm
from collections import Counter

# Model names
model_names = [
    "DGurgurov/xlm-r_telugu_sentiment",
    "cardiffnlp/twitter-xlm-roberta-base-sentiment",
    "ai4bharat/indic-bert"
]

# Load tokenizers and models for all three models
models = []
tokenizers = []

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

for model_name in model_names:
    tokenizers.append(AutoTokenizer.from_pretrained(model_name))
    models.append(AutoModelForSequenceClassification.from_pretrained(model_name).to(device))

# File paths
input_file = "final_dataset.csv"  # Input CSV file
output_file = "three_way_output.csv"  # Output CSV file
error_indices_file = "error_indices.txt"

# Load the input data
df = pd.read_csv(input_file, encoding='utf-8')

# Ensure the output columns exist
if 'label' not in df.columns:
    df['label'] = ''
if 'confidence' not in df.columns:
    df['confidence'] = ''


Some weights of AlbertForSequenceClassification were not initialized from the model checkpoint at ai4bharat/indic-bert and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [22]:
# Function for sentiment classification using hard voting
def classify_text_with_voting(text):
    try:
        votes = []  # Store predictions from all models
        confidence_scores = []  # Store confidence for averaging

        for tokenizer, model in zip(tokenizers, models):
            inputs = tokenizer(text, return_tensors="pt", truncation=True, padding=True).to(device)
            outputs = model(**inputs)
            probabilities = F.softmax(outputs.logits, dim=1)
            
            # Check number of labels for the model
            num_labels = model.config.num_labels
            if num_labels == 2:
                # Binary model output: map to Positive/Negative only
                positive_confidence = probabilities[0, 1].item()
                negative_confidence = probabilities[0, 0].item()

                # Assign Neutral if confidence is low
                if abs(positive_confidence - negative_confidence) < 0.2:  # Threshold for neutrality
                    predicted_class = 1  # Neutral
                else:
                    predicted_class = 0 if negative_confidence > positive_confidence else 2
            else:
                # 3-class model: directly predict
                predicted_class = torch.argmax(probabilities, dim=1).item()

            votes.append(predicted_class)
            confidence_scores.append(probabilities[0, predicted_class].item())

        # Hard voting: Most common label
        final_label = Counter(votes).most_common(1)[0][0]
        avg_confidence = sum(confidence_scores) / len(confidence_scores)

        return final_label, avg_confidence
    except Exception as e:
        print(f"Error during classification: {e}")
        return None, None


In [24]:
error_indices = []

# Process all rows
for i in tqdm(range(len(df)), desc="Processing Sentiment Classification"):
    try:
        text = df.iloc[i]['content']
        if pd.isna(text) or text.strip() == "":
            print(f"Skipping empty content at index {i}")
            continue

        # Perform classification with hard voting
        label, confidence = classify_text_with_voting(text)
        if label is None:
            error_indices.append(i)
            print(f"Classification failed at index {i}, added to error list.")
            continue

        # Update the dataframe with the results
        df.loc[i, 'label'] = label
        df.loc[i, 'confidence'] = confidence
        print(f"Text '{i}' classified as {label} with confidence {confidence:.4f}.")

    except Exception as e:
        print(f"Error at index {i}: {e}")
        error_indices.append(i)
        continue

Processing Sentiment Classification:   0%|          | 0/26150 [00:00<?, ?it/s]Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.
Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.
Processing Sentiment Classification:   0%|          | 3/26150 [00:00<1:15:41,  5.76it/s]

Text '0' classified as 0 with confidence 0.6845.
Error during classification: index 2 is out of bounds for dimension 1 with size 2
Classification failed at index 1, added to error list.
Text '2' classified as 1 with confidence 0.5742.


Processing Sentiment Classification:   0%|          | 5/26150 [00:00<1:13:34,  5.92it/s]

Text '3' classified as 0 with confidence 0.6739.
Text '4' classified as 0 with confidence 0.6519.


Processing Sentiment Classification:   0%|          | 7/26150 [00:01<53:35,  8.13it/s]  

...

Text '26137' classified as 0 with confidence 0.6233.
Error during classification: index 2 is out of bounds for dimension 1 with size 2
Classification failed at index 26138, added to error list.
Error during classification: index 2 is out of bounds for dimension 1 with size 2
Classification failed at index 26139, added to error list.
Text '26140' classified as 1 with confidence 0.5268.
Error during classification: index 2 is out of bounds for dimension 1 with size 2
Classification failed at index 26141, added to error list.


Processing Sentiment Classification: 100%|█████████▉| 26148/26150 [39:18<00:00, 18.05it/s]

Text '26142' classified as 0 with confidence 0.6574.
Error during classification: index 2 is out of bounds for dimension 1 with size 2
Classification failed at index 26143, added to error list.
Error during classification: index 2 is out of bounds for dimension 1 with size 2
Classification failed at index 26144, added to error list.
Error during classification: index 2 is out of bounds for dimension 1 with size 2
Classification failed at index 26145, added to error list.
Error during classification: index 2 is out of bounds for dimension 1 with size 2
Classification failed at index 26146, added to error list.
Text '26147' classified as 1 with confidence 0.6123.


Processing Sentiment Classification: 100%|██████████| 26150/26150 [39:19<00:00, 11.08it/s]

Error during classification: index 2 is out of bounds for dimension 1 with size 2
Classification failed at index 26148, added to error list.
Error during classification: index 2 is out of bounds for dimension 1 with size 2
Classification failed at index 26149, added to error list.


In [25]:
# Save the results
df.to_csv(output_file, index=False)

# Save error indices
if error_indices:
    with open(error_indices_file, "a") as f:
        for index in error_indices:
            f.write(f"{index}\n")

# End time
end_time = strftime("%Y-%m-%d %H:%M:%S", gmtime())
print("Processing complete!")
print(f"Indices with classification errors saved to {error_indices_file}.")
print(f"The end time is {end_time}.")

Processing complete!
Indices with classification errors saved to error_indices.txt.
The end time is 2025-01-09 03:50:14.


In [14]:

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)

cuda


In [16]:
model_names = [
    "DGurgurov/xlm-r_telugu_sentiment",
    "cardiffnlp/twitter-xlm-roberta-base-sentiment",
    "ai4bharat/indic-bert"
]
for model_name, model in zip(model_names, models):
    print(f"Model: {model_name}, Num Labels: {model.config.num_labels}")

Model: DGurgurov/xlm-r_telugu_sentiment, Num Labels: 2
Model: cardiffnlp/twitter-xlm-roberta-base-sentiment, Num Labels: 3
Model: ai4bharat/indic-bert, Num Labels: 2
